# Photoinjector simulation in Volume
Let's simulate a CLEAR-like photoinjector.
We need to use Volume because we need the:
* Full overlap of field maps: electron gun's electric field + solenoid field
* Time integration to correctly model space-charge effects

In [ ]:
%plot -f SVG

In [ ]:
RF_Track;

In [ ]:
addpath('scripts/')

## Define the key parameters

In [ ]:
Setup.Bz = 0.25; % T, solendoid peak field
Setup.Ez = 100; % MV/m, gun gradient
Setup.PHID = 140; % deg, gun phase

Q_pC = 50; % pC, bunch charge extracted
sigr = 0.8; % mmm, laser spot size at cathode
sigt = 1.2; % ps, laser pulse length

## Beam creation at cathode
To create a suitable particles distribution, we can use a generator similar to the ASTRA's one. For more information, see [HERE](https://indico.cern.ch/event/1186676/).

In [ ]:
Nparticles = 5000; % number of macroparticles

%% Beam creation at cathode
G = Bunch6dT_Generator();
G.species = 'electrons';          % species
G.cathode = true;                 % cathode, true or false
G.noise_reduc = true;             % noise reduction (quasi-random)
G.q_total = Q_pC/1e3;             % nC bunch charge
G.ref_ekin = 0;                   % MeV energy of reference particle
G.ref_zpos = 0;                   % m position of reference particle
G.ref_clock = 0;                  % ns clock of reference particle
G.phi_eff = 3.5;                  % eV, effective work function
G.e_photon = 4.73;                % eV, photon energy for Fermi-Dirac distribution.
G.dist_x = 'g';                   % Specifies the transverse particle distribution in the horizontal direction.
G.dist_y = 'g';                   % Specifies the transverse particle distribution in the vertical direction.
G.sig_x = sigr;                   % mm, rms bunch size in the horizontal direction. Also the vertical bunch size if Dist_x = radial.
G.sig_y = sigr;                   % mm, rms bunch size in the vertical direction.
G.sig_t = sigt/1e3;               % ns, rms value of the emission time, i.e. the bunch length if generated from a cathode
G.c_sig_x = 3;                    % cuts off a Gaussian horizontal distribution
G.c_sig_y = 3;                    % cuts off a Gaussian vertical distribution
G.c_sig_t = 3;                    % cuts off a Gaussian longitudinal distribution
G.dist_pz = 'fd_300';             % Emission from cathode following a Fermi-Dirac dist. (for z)
B0 = Bunch6dT (G, Nparticles);

In [ ]:
% Let's display the phase space, which, for a Bunch6dT, is by default X Px Y Py Z Pz

M0 = B0.get_phase_space();
M0(1:10,:)

t0 = B0.get_phase_space('%t0');
hist(t0 / RF_Track.ps, 40)
xlabel('t_0 [ps]')

## We load the gun and the solenoid field maps

In [ ]:
[Gun,GunS] = init_gun (Setup);
[Sol,SolS] = init_solenoid (Setup);

In [ ]:
GunS
SolS

We add the elements to the Volume using: ```V.add (Gun, ...);```
* ```V.add (Gun, X, Y, Z, 'entrance');```
* ```V.add (Gun, X, Y, Z, ROLL, PITCH, YAW, 'entrance');```

In [ ]:
## We define the volume
V = Volume();
V.add (Gun, 0, 0, GunS);
V.add (Sol, 0, 0, SolS);
V.set_s0(0.0); % entrance boundary
V.set_s1(1.0); % exit boundary

In [ ]:
V.get_s0()
V.get_s1()

## Let's plot the fields

In [ ]:
Za = linspace(0, 1000, 500); % mm, Z axis
O = zeros(1,500);
I = ones(1,500);

[E,B] = V.get_field ( O, O, Za, I*40 ); %% X, Y, Z, T

ax = plotyy(Za/1e3, E(:,3)/1e6, Za/1e3, B(:,3));
xlabel('S [m]')
ylabel(ax(1), 'E_z [MV/m]');
ylabel(ax(2), 'B_z [T]');

We need now to setup the tracking options

In [ ]:
V.odeint_algorithm = 'rk2'; % pick your favorite algorithm, 'rk2', 'rkf45', 'leapfrog', 'analytic' are valid options
V.dt_mm = 0.1; % mm/c, integration step size
V.sc_dt_mm = 5; % mm/c, time step of the space-charge effect calculation
V.cfx_dt_mm = 0; % mm/c, time space between two collective effects kicks 
V.tt_dt_mm = 50; % mm/c, time step at which the tranport table is computed
V.t_max_mm = 2000; % mm/c, max tracking time

Now we can perform tracking

In [ ]:
tic
B1 = V.track(B0);
toc

## Phase space plots

In [ ]:
M1 = B1.get_phase_space();
figure
scatter(M1(:,5), M1(:,6));
xlabel('Z [mm]')
ylabel('Pz [MeV/c]')

T = V.get_transport_table('%t %mean_Z %mean_K %emitt_x');
figure
ax = plotyy(T(:,2)/1e3, T(:,3), T(:,2)/1e3, T(:,4));
xlabel('S [m]')
ylabel(ax(1), 'K [MeV]');
ylabel(ax(2), 'emitt_x [mm.mrad]');

Volume uses Z and Pz as longitudinal phase space coordinates (canonical pair)
Lattice uses t and E as longitudinal phase space coordinates (canonical pair)

In [ ]:
B1_6d = V.get_bunch_at_s1();
M1_6d = B1_6d.get_phase_space('%dt %P');

figure
scatter(M1_6d(:,1), M1_6d(:,2));
xlabel('d{t} [mm/c]')
ylabel('P [MeV/c]')

## Adding a Volume to a Lattice
A Volume can be inserted into a Lattice. In this case, the incoming Bunch6d is placed at s0, and the tracking continues in Volume until the particles reach s1.

Let's see an example:

In [ ]:
L = Lattice();
L.append (V);
L.append (LINAC);